In [7]:
import xarray as xr
import os
import numpy as np
import timeit
start_time = timeit.default_timer()

#-- information on simulations to be processed:
IOP = 'ches_IOP2'
em  = 'ensemble.member.8'
path = '/air/lwanner/'+IOP+'/'+em+'/'#'C:/Luise/PALM/CHEESEHEAD_simulations/' #-- on UW Mdison server, this should point to ensemble member directory
# em1: sims = ['01.ches_IOP2.24050','02.ches_IOP2.10023','03.ches_IOP2.28390','04.ches_IOP2.20941','05.ches_IOP2.13864','06.ches_IOP2.31028','07.ches_IOP2.19931','08.ches_IOP2.19743']
# em2: sims = ['01.ches_IOP2.20255','02.ches_IOP2.13449','03.ches_IOP2.733','04.ches_IOP2.18198','05.ches_IOP2.19794','06.ches_IOP2.11638','07.ches_IOP02.31113'] # add other simulations of ensemble member (IOP2 ensemble member 2: (1) 20255 (2) 13449 (3) 733 (4) 18198 (5) 19794 (6) 11638 (7) 31113)
# em3: sims = ['01.ches_IOP2.2199','02.ches_IOP2.11581','03.ches_IOP2.26923','04.ches_IOP2.16339','05.ches_IOP2.10214','06.ches_IOP2.17190','07.ches_IOP2.19176']
# em4: sims = ['01.ches_IOP2.5461','02.ches_IOP2.19281','03.ches_IOP2.11295','04.ches_IOP2.14610','05.ches_IOP2.24393','06. ches_IOP2.29130','07. ches_IOP2.18966']
# em5: sims = ['01.ches_IOP2.27066','02.ches_IOP2.28641','03.ches_IOP2.4709','04.ches_IOP2.26733','05. ches_IOP2.16063','06.ches_IOP2.15821','07.ches_IOP2.28647']
# em6: sims = ['01.ches_IOP2.15881','02.ches_IOP2.16506','03.ches_IOP2.9028','04.ches_IOP2.797','05.ches_IOP2.23005','06.ches_IOP2.24108','07.ches_IOP2.6117']
# em7: sims = ['01.ches_IOP02.12798','02.ches_IOP02.5527','03.ches_IOP02.16221','04.ches_IOP02.30862','05.ches_IOP02.32477','06.ches_IOP02.17608','07.ches_IOP02.29345']
sims = ['1.ches_IOP2.11058','2.ches_IOP2.20781','3.ches_IOP2.1521','04.ches_IOP2.1455','05. ches_IOP2.31525','06.ches_IOP2.1409','07.ches_IOP2.31095']

print(sims)
#-- output files to loop through
fls   = ['ms','pr','pr_c1','ts','ts_c1','xy','xy_c1','3d','3d_c1'] #'ms','3d_p','xy_p'
#-- filenames of output files
flnm  = {'ms':    'DATA_MASK_NETCDF_N03_M',
         'pr':    'DATA_1D_PR_NETCDF_N03slice',
         'pr_c1': 'DATA_1D_PR_NETCDF_N02slice',
         'ts':    'DATA_1D_TS_NETCDF_N03slice',
         'ts_c1': 'DATA_1D_TS_NETCDF_N02slice',
         'xy':    'DATA_2D_XY_AV_NETCDF_N03slice',
         'xy_c1': 'DATA_2D_XY_AV_NETCDF_N02slice',
         #'xy_p':  'DATA_2D_XY_AV_NETCDFslice',
         '3d':    'DATA_3D_AV_NETCDF_N03_M',
         '3d_c1': 'DATA_3D_AV_NETCDF_N02_M',}
         #'3d_p':  'DATA_3D_AV_NETCDF'}
#-- list of towers (masked and 3d output)
ms_lst = ['02','03','06','07','08','09','10','11','12','13','14','15','17'] 
#['01','02','03','04','05','06','07','08','09','10','11','12','13','14','15','16','17','18','19']


['1.ches_IOP2.11058', '2.ches_IOP2.20781', '3.ches_IOP2.1521', '04.ches_IOP2.1455', '05. ches_IOP2.31525', '06.ches_IOP2.1409', '07.ches_IOP2.31095']


In [8]:
#-- loop through different types of output files and combine them
for f in range(len(fls)):
    #-- if dataset is masked output, extract y amd x information of tower locations for later
    if (fls[f] == 'ms') or (fls[f] == '3d') or (fls[f] == '3d_c1'):
        for i in range(len(ms_lst)):
            #-- make list of files of that type of output that belong to the ensemble member
            files = []
            for s in np.arange(len(sims)):
                files.append(path+sims[s]+'/'+flnm[fls[f]]+ms_lst[i]+'slice_subsetLW')
            #-- read in this type of output file from all simulations of one ensemble member
            combined = xr.open_mfdataset(files,decode_times=None,engine='netcdf4')
            #-- store combined output
            print('saving '+path+flnm[fls[f]]+ms_lst[i]+'_'+IOP+'_'+em)
            combined.to_netcdf(path+flnm[fls[f]]+ms_lst[i]+'_'+IOP+'_'+em,engine='netcdf4')
            combined.close()
            #-- delete input files (output files from single simulations) to reduce data volume. If needed, rerun extractCHEESEHEAD_cheyenne2.py to recreate them.
            for s in np.arange(len(files)):
                if os.path.isfile(files[s]):
                    print('deleting '+files[s])
                    os.remove(files[s])
    else:
        #-- make list of files of that type of output that belong to the ensemble member
        files = []
        for s in np.arange(len(sims)):
            files.append(path+sims[s]+'/'+flnm[fls[f]]+'_subsetLW')
        #-- read in this type of output file from all simulations of one ensemble member
        combined = xr.open_mfdataset(files,decode_times=None,engine='netcdf4')
        #-- store combined output
        print('saving '+path+flnm[fls[f]]+'_'+IOP+'_'+em)
        combined.to_netcdf(path+flnm[fls[f]]+'_'+IOP+'_'+em,engine='netcdf4')
        combined.close()
        #-- delete input files (output files from single simulations) to reduce data volume. If needed, rerun extractCHEESEHEAD_cheyenne2.py to recreate them.
        for s in np.arange(len(files)):
            if os.path.isfile(files[s]):
                print('deleting '+files[s])
                os.remove(files[s])

        
elapsed = timeit.default_timer() - start_time
print('Time elapsed:',elapsed, 'seconds')
print('Done!')

saving /air/lwanner/ches_IOP2/ensemble.member.8/DATA_3D_AV_NETCDF_N02_M02_ches_IOP2_ensemble.member.8
deleting /air/lwanner/ches_IOP2/ensemble.member.8/1.ches_IOP2.11058/DATA_3D_AV_NETCDF_N02_M02slice_subsetLW
deleting /air/lwanner/ches_IOP2/ensemble.member.8/2.ches_IOP2.20781/DATA_3D_AV_NETCDF_N02_M02slice_subsetLW
deleting /air/lwanner/ches_IOP2/ensemble.member.8/3.ches_IOP2.1521/DATA_3D_AV_NETCDF_N02_M02slice_subsetLW
deleting /air/lwanner/ches_IOP2/ensemble.member.8/04.ches_IOP2.1455/DATA_3D_AV_NETCDF_N02_M02slice_subsetLW
deleting /air/lwanner/ches_IOP2/ensemble.member.8/05. ches_IOP2.31525/DATA_3D_AV_NETCDF_N02_M02slice_subsetLW
deleting /air/lwanner/ches_IOP2/ensemble.member.8/06.ches_IOP2.1409/DATA_3D_AV_NETCDF_N02_M02slice_subsetLW
deleting /air/lwanner/ches_IOP2/ensemble.member.8/07.ches_IOP2.31095/DATA_3D_AV_NETCDF_N02_M02slice_subsetLW
saving /air/lwanner/ches_IOP2/ensemble.member.8/DATA_3D_AV_NETCDF_N02_M03_ches_IOP2_ensemble.member.8
deleting /air/lwanner/ches_IOP2/ensemb